### Preprocesamiento
Aqui se detalla paso por paso como se limpia los datos

In [1]:
import pandas as pd
from opencage.geocoder import OpenCageGeocode
import json

### Limpieza de datos
Por orden:
- Conversión de valor de texto de los test a enteros 
- Asignar 'Zalamea De La Serena' al codigo postal 6430 
- Descartar filas sin codigo postal ni geo location

In [ ]:
# Leer el archivo CSV
file_path = "../data/raw/new_data.csv" 
data = pd.read_csv(file_path, dtype={'Postal code': str})
data["Postal code"] = data["Postal code"].astype(str).str.zfill(5)

print(data.head())

0
Date                                   ﻿"2020-07-20 12:59:04"
Geo Location    {"latitude":41.6276264,"longitude":2.2947037}
Name test                                          Leishmania
Value test                                           Negativo
Pet sex                                                   NaN
Pet age                                                 Año/s
Country                                                 Spain
City                                                Barcelona
Postal code                                             08520
Name: 0, dtype: object
1
Date                                   ﻿"2020-07-20 12:59:25"
Geo Location    {"latitude":41.6274545,"longitude":2.2949996}
Name test                                          Leishmania
Value test                                           Negativo
Pet sex                                                   NaN
Pet age                                                 Año/s
Country                                    

KeyboardInterrupt: 

In [ ]:
# Convertir valores de 'Value test'
data['Value test'] = data['Value test'].fillna(0).astype(int)

print(data.head())

                     Date                                   Geo Location  \
0  ﻿"2020-07-20 12:59:04"  {"latitude":41.6276264,"longitude":2.2947037}   
1  ﻿"2020-07-20 12:59:25"  {"latitude":41.6274545,"longitude":2.2949996}   
2  ﻿"2020-07-20 13:18:08"  {"latitude":41.6274519,"longitude":2.2949754}   
3  ﻿"2020-07-20 13:19:02"  {"latitude":41.6274799,"longitude":2.2950886}   
4  ﻿"2020-07-20 13:37:12"  {"latitude":41.6274648,"longitude":2.2950282}   

    Name test  Value test Pet sex Pet age Country       City Postal code  
0  Leishmania           0     NaN   Año/s   Spain  Barcelona       08520  
1  Leishmania           0     NaN   Año/s   Spain  Barcelona       08520  
2  Leishmania           0     NaN   Año/s   Spain  Barcelona       08520  
3  Leishmania           0     NaN   Año/s   Spain  Barcelona       08520  
4  Leishmania           0     NaN   Año/s   Spain  Barcelona       08520  


In [54]:
# Eliminar filas donde ambas variables 'Postal code' y 'Geo Location' estén vacías
data_cleaned = data[~(data["Postal code"].isnull() & data["Geo Location"].isnull())]

print(data_cleaned[data_cleaned['Postal code'].isnull()])
print(data_cleaned[data_cleaned['Geo Location'].isnull()])

Empty DataFrame
Columns: [Date, Geo Location, Name test, Value test, Pet sex, Pet age, Country, City, Postal code]
Index: []
                         Date Geo Location   Name test  Value test Pet sex  \
156    ﻿"2021-04-14 13:49:16"          NaN  Leishmania           1     NaN   
157    ﻿"2021-04-14 13:51:29"          NaN  Leishmania           1     NaN   
158    ﻿"2021-04-14 13:55:49"          NaN  Leishmania           1     NaN   
159    ﻿"2021-05-11 11:59:22"          NaN     Giardia           1     NaN   
160    ﻿"2021-05-11 12:03:12"          NaN     Giardia           1     NaN   
...                       ...          ...         ...         ...     ...   
42773  ﻿"2024-10-30 18:25:40"          NaN  Leishmania           0   Macho   
42792  ﻿"2024-10-31 11:01:17"          NaN     Giardia           0  Hembra   
42812  ﻿"2024-10-31 13:15:35"          NaN  Leishmania           0   Macho   
42813  ﻿"2024-10-31 13:16:19"          NaN  Leishmania           0  Hembra   
42817  ﻿"2024-10-

In [50]:
# Modificar 'City' si el código postal es 6430
data_cleaned['City'] = data_cleaned.apply(
    lambda row: 'Zalamea De La Serena' if row['Postal code'] == '06430' else row['City'], axis=1
)

print(data_cleaned[data_cleaned['Postal code'] == '06430'].head(10))

                         Date                                    Geo Location  \
13856  ﻿"2023-01-09 16:44:47"                                             NaN   
14100  ﻿"2023-01-14 12:45:38"  {"latitude":38.6512999,"longitude":-5.6544715}   
14101  ﻿"2023-01-14 12:49:50"  {"latitude":38.6512707,"longitude":-5.6544525}   
14102  ﻿"2023-01-14 12:52:32"  {"latitude":38.6512707,"longitude":-5.6544525}   
14556  ﻿"2023-01-25 16:54:25"  {"latitude":38.6513201,"longitude":-5.6544319}   
16887  ﻿"2023-03-08 19:50:23"  {"latitude":38.6512569,"longitude":-5.6545199}   
17714  ﻿"2023-03-21 18:36:03"  {"latitude":38.6512222,"longitude":-5.6545374}   
17924  ﻿"2023-03-24 10:50:13"   {"latitude":38.651208,"longitude":-5.6545264}   
17925  ﻿"2023-03-24 10:52:17"   {"latitude":38.651208,"longitude":-5.6545264}   
17928  ﻿"2023-03-24 10:54:18"   {"latitude":38.651208,"longitude":-5.6545264}   

        Name test  Value test Pet sex  Pet age Country                  City  \
13856  Leishmania           

Calcular la prevalencia y la cantidad de positivos que hay

     Postal code  Value test
1          01002           3
2          01004           1
3          01006           3
4          01012           1
10         02400           1
...          ...         ...
1226       50620           2
1231       50800           1
1232       50830          10
1233       52005           2
1234       52006           2

[631 rows x 2 columns]


### Correccion de datos
En esta parte se hace consultas a la api de "open cage data" (https://opencagedata.com/) para aquellas columnas que tienen geo location pero no tienen codigo postal se obtengan mediante la api

In [10]:
# Inicializa el geocoder con la clave de API
OCG = OpenCageGeocode('e5133987de494dd393d5de1370554b2f')

In [11]:
# Función para obtener el código postal a partir de Geo Location
def get_postal_code(geo_location):
    try:
        # Convertir la cadena JSON en un diccionario
        location = json.loads(geo_location)
        lat = location['latitude']
        lng = location['longitude']
        # Realizar la búsqueda inversa
        results = OCG.reverse_geocode(lat, lng)
        if results and 'postcode' in results[0]['components']:
            return results[0]['components']['postcode']
    except Exception as e:
        print(f"Error procesando {geo_location}: {e}")
    return None

In [52]:
print(data_cleaned[data_cleaned['Postal code'].isnull()])

Empty DataFrame
Columns: [Date, Geo Location, Name test, Value test, Pet sex, Pet age, Country, City, Postal code]
Index: []


In [56]:
# Agregar códigos postales donde faltan pero existe Geo Location
data_cleaned['Postal code'] = data_cleaned.apply(
    lambda row: get_postal_code(row['Geo Location']) if pd.isna(row['Postal code']) and pd.notna(row['Geo Location']) else row['Postal code'],
    axis=1
)

Hace consultas a la api de "open cage data" (https://opencagedata.com/) para aquellas columnas que tienen geo location pero no tienen geolocalizacion y la obtiene a traves de su codigo postal.

Agrupa en el csv archivo agrupado todos los codigos postales y suma el valor de los resultados de los tests.

In [58]:
def get_geo_location(postal_code):
    try:
        # Convertir el código postal a cadena
        postal_code_str = str(int(postal_code))  # Eliminar decimales innecesarios
        results = OCG.geocode(postal_code_str)
        if results:
            lat = results[0]['geometry']['lat']
            lng = results[0]['geometry']['lng']
            return f"{lat},{lng}"
    except Exception as e:
        print(f"Error procesando {postal_code}: {e}")
    return None

In [59]:
print(data_cleaned[data_cleaned['Geo Location'].isnull()])

                         Date Geo Location   Name test  Value test Pet sex  \
156    ﻿"2021-04-14 13:49:16"          NaN  Leishmania           1     NaN   
157    ﻿"2021-04-14 13:51:29"          NaN  Leishmania           1     NaN   
158    ﻿"2021-04-14 13:55:49"          NaN  Leishmania           1     NaN   
159    ﻿"2021-05-11 11:59:22"          NaN     Giardia           1     NaN   
160    ﻿"2021-05-11 12:03:12"          NaN     Giardia           1     NaN   
...                       ...          ...         ...         ...     ...   
42773  ﻿"2024-10-30 18:25:40"          NaN  Leishmania           0   Macho   
42792  ﻿"2024-10-31 11:01:17"          NaN     Giardia           0  Hembra   
42812  ﻿"2024-10-31 13:15:35"          NaN  Leishmania           0   Macho   
42813  ﻿"2024-10-31 13:16:19"          NaN  Leishmania           0  Hembra   
42817  ﻿"2024-10-31 13:54:42"          NaN  Leishmania           0   Macho   

        Pet age Country        City Postal code  
156       Año

In [ ]:
# Rellenar la columna 'Geo Location' donde falte pero exista 'Postal code'
data_cleaned['Geo Location'] = data_cleaned.apply(
    lambda row: get_geo_location(row['Postal code']) if pd.isna(row['Geo Location']) and pd.notna(row['Postal code']) else row['Geo Location'],
    axis=1
)

In [ ]:
# Agrupar por 'Postal code' y sumar los valores de 'Value test'
grouped_data = data_cleaned.groupby('Postal code', as_index=False).agg({
    'Value test': 'sum',  # Sumar los valores de Value test
    'City': 'first',  # Mantener el primer valor de City por grupo
    'Geo Location': 'first',  # Mantener el primer valor de Geo Location por grupo
})

In [ ]:
# Guardar el archivo agrupado con las sumas
grouped_output_path = "data/archivo_agrupado.csv"
grouped_data.to_csv(grouped_output_path, index=False)

# Guardar el archivo completo procesado
processed_output_path = "data/archivo_completo.csv"
data_cleaned.to_csv(processed_output_path, index=False)


Crea un nuevo csv agrupando por codigo postal y guardando el numero de apariciones de cada tipo de resultado por codigo postal.

In [75]:
# Crear un contador de cada tipo de resultado por código postal
result_counts = data_cleaned.pivot_table(
    index='Postal code',  # Agrupar por código postal
    columns='Value test',  # Contar por cada tipo de resultado
    aggfunc='size',  # Contar las ocurrencias
    fill_value=0  # Rellenar los valores faltantes con 0
).reset_index()

In [76]:
# Renombrar las columnas para mayor claridad
result_counts.columns.name = None  # Quitar el nombre del índice de columnas
result_counts.rename(columns={
    -2: 'Dudoso',
    -1: 'Error',
    0: 'Negativo',
    1: 'Positivo',
    2: 'Positivo Fuerte'
}, inplace=True)

In [77]:
# Agregar columnas faltantes con 0 si no existen en los datos
for col in ['Dudoso', 'Error', 'Invalido', 'Inválido', 'Negativo', 'Positivo', 'Positivo Fuerte']:
    if col not in result_counts.columns:
        result_counts[col] = 0

# Reordenar las columnas
result_counts = result_counts[['Postal code', 'Dudoso', 'Error', 'Invalido', 'Inválido', 'Negativo', 'Positivo', 'Positivo Fuerte']]

In [78]:
# Guardar el resultado en un nuevo archivo CSV
output_path = "data/all_results_by_postal_code.csv"
result_counts.to_csv(output_path, index=False)